## Load Libraries

In [ ]:
import time
import numpy as np

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

from tensorflow.keras.layers import *
from tensorflow.keras.models import Model

from tensorflow.keras.callbacks import EarlyStopping
from sklearn.model_selection import *
from utils import *
import tensorflow.keras.backend as K


In [ ]:
CE = np.load('/workspace/data/EEG/data/epochs/A-epo.npy')
lab = np.load("/workspace/data/EEG/data/epochs/A-labels.npy")

In [2]:
tCE = np.transpose(CE,(0,1,3,2))

In [3]:

def SepConv1D(Chans = 6, Samples = 206, Filters = 32):
  eeg_input    = Input(shape = (Samples, Chans))

  padded       = ZeroPadding1D(padding = 4)(eeg_input)
  block1       = SeparableConv1D(Filters, 16, strides = 8,
                                 padding = 'valid',
                                 data_format = 'channels_last',
                                 kernel_initializer = 'glorot_uniform',
                                 bias_initializer = 'zeros',
                                 use_bias = True)(padded)
  block1       = Activation('tanh')(block1)
  flatten      = Flatten(name = 'flatten')(block1)
  prediction   = Dense(1, activation = 'sigmoid')(flatten)

  return Model(inputs = eeg_input, outputs = prediction, name='SepConv1D')

In [4]:


def evaluate_subject_models(data, labels, modelpath, subject, n_filters = 16):
    """
    Trains and evaluates P300-CNNT for each subject in the P300 Speller database
    using repeated stratified K-fold cross validation.
    """
    n_sub = data.shape[0]
    n_trials = data.shape[1]
    n_samples = data.shape[2]
    n_channels = data.shape[3]

    inf_time = np.zeros(5 * 10)
    aucs = np.zeros(5 * 10)

    print("Training for subject {0}: ".format(subject))
    cv = RepeatedStratifiedKFold(n_splits = 5, n_repeats = 10, random_state = 123)
    for k, (t, v) in enumerate(cv.split(data[subject], labels[subject])):
        X_train, y_train, X_test, y_test = data[subject, t, :, :], labels[subject, t], data[subject, v, :, :], labels[subject, v]
        X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size = 0.2, shuffle = True, random_state = 456)
        print('Partition {0}: X_train = {1}, X_valid = {2}, X_test = {3}'.format(k, X_train.shape, X_valid.shape, X_test.shape))

        # channel-wise feature standarization
        sc = EEGChannelScaler(n_channels = n_channels)
        X_train = sc.fit_transform(X_train)
        X_test = sc.transform(X_test)

        #tt = TrainTime()

        model = SepConv1D(Chans = n_channels, Samples = n_samples, Filters = n_filters)
        print(model.summary())
        model.compile(optimizer = 'adam', loss = 'binary_crossentropy')

        # Early stopping setting also follows EEGNet (Lawhern et al., 2018)
        es = EarlyStopping(monitor = 'val_loss', mode = 'min', patience = 50, restore_best_weights = True)

        start_train = time.time()
        history = model.fit(X_train,
                            y_train,
                            batch_size = 256,
                            epochs = 200,
                            validation_data = (X_valid, y_valid),
                            callbacks = [es])
        train_time = time.time()-start_train

        start_test = time.time()
        proba_test = model.predict(X_test)
        test_time =  time.time() - start_test

        test_size = X_test.shape[0]
        inf_time[k] = test_time/test_size

        aucs[k] = roc_auc_score(y_test, proba_test)
        print('S{0}, P{1} -- AUC: {2}'.format(subject, k, aucs[k]))
        K.clear_session()

    np.savetxt(modelpath + '/s' + str(subject) + '_auc.npy', aucs)
    np.savetxt(modelpath + '/inf_time.npy', inf_time)

    np.save(modelpath + '/s' + str(subject) + '_data.npy', X_test)
    np.save(modelpath + '/s' + str(subject) + '_labels.npy', y_test)
    model.save_weights(modelpath + '/s' + str(subject) + '_model.h5')

    #return aucs, train_time, inf_time

In [14]:
import time
def evaluate_cross_subject_model(data, labels, modelpath, n_filters = 32):
    """
    Trains and evaluates SepConv1D for each subject in the P300 Speller database
    using random cross validation.
    """
    n_sub = data.shape[0]
    n_ex_sub = data.shape[1]
    n_samples = data.shape[2]
    n_channels = data.shape[3]

    aucs = np.zeros(n_sub)
    inf_time = np.zeros(n_sub)


    data = data.reshape((n_sub * n_ex_sub, n_samples, n_channels))
    labels = labels.reshape((n_sub * n_ex_sub))
    groups = np.array([i for i in range(n_sub) for j in range(n_ex_sub)])

    cv = LeaveOneGroupOut()
    for k, (t, v) in enumerate(cv.split(data, labels, groups)):
        X_train, y_train, X_test, y_test = data[t], labels[t], data[v], labels[v]
        rg = np.random.choice(t, 1)
        sv = groups[t] == groups[rg]
        st = np.logical_not(sv)
        X_train, y_train, X_valid, y_valid = data[t][st], labels[t][st], data[t][sv], labels[t][sv]
        print("Partition {0}: train = {1}, valid = {2}, test = {3}".format(k, X_train.shape, X_valid.shape, X_test.shape))
        print("Groups train = {0}, valid = {1}, test = {2}".format(np.unique(groups[t][st]),
                                                                   np.unique(groups[t][sv]),
                                                                   np.unique(groups[v])))

         # channel-wise feature standarization
        sc = EEGChannelScaler(n_channels = n_channels)
        X_train = sc.fit_transform(X_train)
        X_valid = sc.transform(X_valid)
        X_test = sc.transform(X_test)

        model = SepConv1D(Chans = n_channels, Samples = n_samples, Filters = n_filters)
        print(model.summary())
        model.compile(optimizer = 'adam', loss = 'binary_crossentropy')

        es = EarlyStopping(monitor = 'val_loss', mode = 'min', patience = 50, restore_best_weights = True)

        start_train = time.time()
        model.fit(X_train,
                  y_train,
                  batch_size = 256,
                  epochs = 200,
                  validation_data = (X_valid, y_valid),
                  callbacks = [es])
        train_time = time.time()-start_train

        start_test = time.time()
        proba_test = model.predict(X_test)
        test_time = time.time() - start_test

        test_size = X_test.shape[0]
        inf_time[k] = test_time/test_size


        aucs[k] = roc_auc_score(y_test, proba_test)
        print('P{0} -- AUC: {1}'.format(k, aucs[k]))
        model.save_weights(modelpath + '/s' + str(np.unique(groups[v])[0]) + '_model.h5')
        np.save(modelpath + '/s' + str(np.unique(groups[v])[0]) + '_data.npy', X_test)
        np.save(modelpath + '/s' + str(np.unique(groups[v])[0]) + '_labels.npy', y_test)
        K.clear_session()

    np.savetxt(modelpath + '/aucs.npy', aucs)
    np.savetxt(modelpath + '/inf_time.npy', inf_time)

    return aucs, train_time, inf_time

In [5]:
within_modelpath = "/workspace/data/EEG/models/sepconv1d/within/"
cross_modelpath = "/workspace/data/EEG/models/sepconv1d/cross/"

## Within Subject Training

In [12]:
auc_Wsuv, Wtrain_time, Winf_time = evaluate_subject_models(tCE, lab, within_modelpath, 0)

Training for subject 0: 
Partition 0: X_train = (2688, 257, 8), X_valid = (672, 257, 8), X_test = (840, 257, 8)
Model: "SepConv1D"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 257, 8)]          0         
                                                                 
 zero_padding1d (ZeroPadding  (None, 265, 8)           0         
 1D)                                                             
                                                                 
 separable_conv1d (Separable  (None, 32, 32)           416       
 Conv1D)                                                         
                                                                 
 activation (Activation)     (None, 32, 32)            0         
                                                                 
 flatten (Flatten)           (None, 1024)              0         
           

In [6]:
for i in range(8):
    evaluate_subject_models(tCE, lab, within_modelpath, i)


Training for subject 0: 
Partition 0: X_train = (2688, 257, 8), X_valid = (672, 257, 8), X_test = (840, 257, 8)
Model: "SepConv1D"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 257, 8)]          0         
                                                                 
 zero_padding1d (ZeroPadding  (None, 265, 8)           0         
 1D)                                                             
                                                                 
 separable_conv1d (Separable  (None, 32, 16)           272       
 Conv1D)                                                         
                                                                 
 activation (Activation)     (None, 32, 16)            0         
                                                                 
 flatten (Flatten)           (None, 512)               0         
           

2022-03-22 03:13:13.048694: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-03-22 03:13:13.798031: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1525] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 30988 MB memory:  -> device: 0, name: Tesla V100-SXM3-32GB, pci bus id: 0000:bc:00.0, compute capability: 7.0
2022-03-22 03:13:15.291299: I tensorflow/stream_executor/cuda/cuda_dnn.cc:368] Loaded cuDNN version 8101
2022-03-22 03:13:15.753752: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory


11/11 [==============================] - 2s 19ms/step - loss: 0.6929 - val_loss: 0.7494
Epoch 2/200
11/11 [==============================] - 0s 7ms/step - loss: 0.6470 - val_loss: 0.7103
Epoch 3/200
11/11 [==============================] - 0s 7ms/step - loss: 0.5963 - val_loss: 0.6776
Epoch 4/200
11/11 [==============================] - 0s 7ms/step - loss: 0.5312 - val_loss: 0.6382
Epoch 5/200
11/11 [==============================] - 0s 7ms/step - loss: 0.4584 - val_loss: 0.5957
Epoch 6/200
11/11 [==============================] - 0s 7ms/step - loss: 0.3963 - val_loss: 0.5598
Epoch 7/200
11/11 [==============================] - 0s 7ms/step - loss: 0.3551 - val_loss: 0.5437
Epoch 8/200
11/11 [==================

In [13]:
print("WITHIN SUBJECT - Average AUC: ", np.mean(auc_Wsuv))
print("WITHIN SUBJECT - Total training time per subject: ", Wtrain_time, "minutes")
print("WITHIN SUBJECT - Inference time per sample: ", np.mean(Winf_time)*60, "seconds")

WITHIN SUBJECT - Average AUC:  0.870079387755102
WITHIN SUBJECT - Total training time per subject:  5.077412366867065 minutes
WITHIN SUBJECT - Inference time per sample:  0.009690891674586706 seconds


## Cross Subject Training

In [21]:
auc_Csub, train_time, inf_time = evaluate_cross_subject_model(tCE, lab, cross_modelpath, n_filters = 32)


Partition 0: train = (25200, 257, 8), valid = (4200, 257, 8), test = (4200, 257, 8)
Groups train = [1 2 3 4 5 6], valid = [7], test = [0]
Model: "SepConv1D"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_3 (InputLayer)        [(None, 257, 8)]          0         
                                                                 
 zero_padding1d_2 (ZeroPaddi  (None, 265, 8)           0         
 ng1D)                                                           
                                                                 
 separable_conv1d_2 (Separab  (None, 32, 32)           416       
 leConv1D)                                                       
                                                                 
 activation_2 (Activation)   (None, 32, 32)            0         
                                                                 
 flatten (Flatten)           (None, 1024)          

In [ ]:
print("CROSS SUBJECT - Average AUC: ", np.mean(auc_Csub))
print("CROSS SUBJECT - Total training time: ", Ctrain_time, "minutes")
print("CROSS SUBJECT - Inference time per sample: ", np.mean(Cinf_time)*60, "seconds")

In [8]:
import argparse
import sys
import numpy as np
import matplotlib
matplotlib.use('Agg')
import matplotlib.pyplot as plt


def plot_aucs(aucpath, filepath, TITLE):
    """
    Plot AUCs
    """
    data_to_plot = []
    aucs = np.zeros((8,50))
    for i in range(8):
        aucs[i, :] = np.loadtxt(aucpath + '/s' + str(i) + '_auc.npy')
        data_to_plot.append(np.loadtxt(aucpath + '/s' + str(i) + '_auc.npy'))

    fig = plt.figure(1, figsize=(9, 6))
    ax = fig.add_subplot(111)
    bp = ax.boxplot(data_to_plot, showmeans=True, meanline=True)
    plt.title(TITLE + "\n Mean AUC:" + str('%.2f' %np.mean(aucs)) + u"\u00B1" + str('%.2f' %np.std(aucs)))
    plt.ylabel("AUC")
    plt.xlabel('Subjects')
    plt.grid(False)
    plt.savefig(filepath)
    return np.mean(aucs), np.std(aucs)

In [9]:
mean_auc, std_auc = plot_aucs(within_modelpath, within_modelpath+"sepconv1d_Wauc.png", "SepConv1d - Within")

In [11]:
mean_auc, std_auc

(0.6945595535714287, 0.08615522947847716)

In [10]:
Caucs = np.loadtxt(cross_modelpath+"aucs.npy")

In [27]:
plt.show()

AttributeError: 'numpy.ndarray' object has no attribute 'index'

In [2]:
%matplotlib inline

import numpy as np
import matplotlib
matplotlib.use('Agg')
import matplotlib.pyplot as plt
Caucs = np.loadtxt("/workspace/data/EEG/models/EEGNet/cross/aucs.npy")

fig = plt.figure(1, figsize=(9, 6))
ax = fig.add_subplot(111)
#bp = ax.barplot(Caucs, showmeans=True, meanline=True)
plt.bar([1,2,3,4,5,6,7,8], Caucs)
plt.title("EEGNet - Cross \n Mean AUC:" + str('%.2f' %np.mean(Caucs)) + u"\u00B1" + str('%.2f' %np.std(Caucs)) )
plt.ylabel("AUC")
plt.xlabel('Subjects')
plt.grid(False)
#plt.show()

plt.savefig("/workspace/data/EEG/models/EEGNet/cross/" + "EEGNet_Cauc.png")




